In [ ]:
import serial
import time
import pandas as pd
import numpy as np
import pyautogui
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
import joblib
from collections import deque

# Configuration du port série
serial_port = 'COM6'
baud_rate = 115200

# Charger le modèle, le scaler, et le label encoder
model = joblib.load('model_simple.joblib')
scaler = joblib.load('scaler_simple.joblib')
label_encoder = joblib.load('label_encoder_simple.joblib')

# Paramètres de la fenêtre
window_size = 50
data_window = deque(maxlen=window_size)

# Noms des colonnes
time_column = ['Time_ms']
sensor_columns = ['AccelX', 'AccelY', 'AccelZ', 'GyroX', 'GyroY', 'GyroZ']

# Caractéristiques des capteurs et du temps
stats_names = ['mean', 'std', 'min', 'max', 'median', 'iqr', 'skew', 'kurt', 'energy', 'topFreq1', 'topFreq2', 'topFreq3']
time_feature_names = ['Time_duration', 'Time_mean_interval', 'Time_std_interval']
sensor_feature_names = [f"{col}_{stat}" for col in sensor_columns for stat in stats_names]
all_feature_names = time_feature_names + sensor_feature_names

# Fichier journal
log_file = "movement_log.csv"
log_columns = time_column + sensor_columns + ["Movement"]
log_data = []

# Seuils pour validation
THRESHOLDS = {
    "Accel": (-20, 20),
    "Gyro": (-2000, 2000)
}

# Filtre passe-bas
def low_pass_filter(data, alpha=0.1):
    filtered = [data[0]]
    for i in range(1, len(data)):
        filtered.append(alpha * data[i] + (1 - alpha) * filtered[i - 1])
    return filtered

# Validation des données
def validate_data(data_values):
    if len(data_values) != 7:  # 1 timestamp + 6 capteurs
        return False
    accel_gyro_values = data_values[1:]  # Exclure le timestamp
    for i, val in enumerate(accel_gyro_values):
        if i < 3:  # Accel
            if not (THRESHOLDS["Accel"][0] <= val <= THRESHOLDS["Accel"][1]):
                return False
        else:  # Gyro
            if not (THRESHOLDS["Gyro"][0] <= val <= THRESHOLDS["Gyro"][1]):
                return False
    return True

# Calcul des caractéristiques temporelles
def compute_time_features(time_data):
    duration = time_data[-1] - time_data[0]  # Durée totale
    intervals = np.diff(time_data)
    mean_interval = intervals.mean() if len(intervals) > 0 else 0
    std_interval = intervals.std() if len(intervals) > 0 else 0
    return [duration, mean_interval, std_interval]

# Calcul des caractéristiques des capteurs
def compute_sensor_features(df, cols):
    features = []
    for col in cols:
        col_data = df[col].values
        col_data_filtered = np.array(low_pass_filter(col_data))
        
        # Calcul des statistiques
        mean_val = col_data_filtered.mean()
        std_val = col_data_filtered.std()
        min_val = col_data_filtered.min()
        max_val = col_data_filtered.max()
        median_val = np.median(col_data_filtered)
        iqr_val = np.percentile(col_data_filtered, 75) - np.percentile(col_data_filtered, 25)
        skew_val = pd.Series(col_data_filtered).skew()
        kurt_val = pd.Series(col_data_filtered).kurt()
        energy_val = np.sum(col_data_filtered**2)
        
        # Transformée de Fourier
        fft_vals = np.fft.rfft(col_data_filtered)
        fft_ampl = np.abs(fft_vals)
        top_freqs = np.sort(fft_ampl)[-3:]  # 3 plus grandes amplitudes
        
        features.extend([mean_val, std_val, min_val, max_val, median_val, iqr_val,
                         skew_val, kurt_val, energy_val] + list(top_freqs))
    return features

# Extraction des caractéristiques
def extract_features_from_window(window_data):
    df = pd.DataFrame(window_data, columns=time_column + sensor_columns)
    time_data = df['Time_ms'].values
    time_feats = compute_time_features(time_data)
    df_sensors = df[sensor_columns]
    sensor_feats = compute_sensor_features(df_sensors, sensor_columns)
    feats = time_feats + sensor_feats
    features_df = pd.DataFrame([feats], columns=all_feature_names)
    return features_df

# Prédiction des mouvements
def predict_movement_filtered(data_values):
    data_window.append(data_values)
    if len(data_window) == window_size:
        features_df = extract_features_from_window(data_window)
        X_new_scaled = scaler.transform(features_df)
        y_pred = model.predict(X_new_scaled)
        movement = label_encoder.inverse_transform(y_pred)
        data_window.clear()
        return movement[0]
    return None

# Mappage des mouvements aux touches
movement_to_key = {
    "Mouvement_1_Horizontal": "u",
    "Mouvement_2_Horizontal_Alt": "j",
    "Mouvement_3_Bloquage": "o",
    "Mouvement_4_estoc": "l",
    "Mouvement_5_vertical": "i",
    "Mouvement_6_vertical_alt": "k",
    "Mouvement_9_Pas_de_Mouvement": "1"
}

# Connexion série
ser = serial.Serial(serial_port, baud_rate)
time.sleep(2)

print("Début de la détection. Appuyez sur Ctrl+C pour arrêter.")

try:
    while True:
        line = ser.readline().decode('utf-8').strip()
        if line and ',' in line:
            parts = line.split(',')
            try:
                data_values = list(map(float, parts))
                if validate_data(data_values):
                    log_data.append(data_values)
                    movement = predict_movement_filtered(data_values)
                    if movement is not None:
                        print(f"Mouvement détecté : {movement}")
                        log_data[-1].append(movement)
                        if movement in movement_to_key and movement_to_key[movement]:
                            pyautogui.press(movement_to_key[movement])
                else:
                    print("Données invalides, ignorées.")
            except ValueError as e:
                print(f"Erreur de conversion : {e}, Ligne : {parts}")
        else:
            print("Ligne vide ou sans virgule, ignorée.")
except KeyboardInterrupt:
    print("Arrêt de la détection.")
finally:
    ser.close()
    if log_data:
        df_log = pd.DataFrame(log_data, columns=log_columns)
        df_log.to_csv(log_file, index=False)
        print(f"Journal sauvegardé dans {log_file}.")


Début de la détection. Appuyez sur Ctrl+C pour arrêter.
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_2_Horizontal_Alt
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_2_Horizontal_Alt
Mouvement détecté : Mouvement_2_Horizontal_Alt
Mouvement détecté : Mouvement_4_estoc
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_5_vertical
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_4_estoc
Mouvement détecté : Mouvement_4_estoc
Mouvement détecté : Mouvement_4_estoc
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_4_estoc
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvement détecté : Mouvement_4_estoc
Mouvement détecté : Mouvement_4_estoc
Mouvement détecté : Mouvement_9_Pas_de_Mouvement
Mouvem

SerialException: GetOverlappedResult failed (PermissionError(13, 'Accès refusé.', None, 5))

In [ ]:
pppppp11